# Make a model & Run it with OpenSEES

This code accepts user input of a simple span multi-girder bridge parameters, then builds and analyzes a static model using the OpenSEES software through the python module OpenSeesPy.

Model plots are generated in Plotly.

To do:
   - Results extraction
   - Compute composite moment
   - consider using stiff beam rather than links to connect to BC to enable extraction
   - Compare to strand7 (check analysis)
   - write the text describing the situation
   - get better at markdown



In [185]:
#Imports

#Plotly for interactive plots
import plotly.offline as py
import plotly.graph_objs as go
py.init_notebook_mode(connected=True)
#Numpy for arrays used in the mesh plots
import numpy as np
#functools.reduce used to flatten list of lists
import functools
#prettyprint
import pprint
pp = pprint.PrettyPrinter(indent=4)
#sys to set path to opensees
import sys
sys.path.append(r'C:\Users\tgolecki\AppData\Local\Continuum\anaconda3\Lib\site-packages\openseespy')
#Opensees for FEA
import opensees
#copy used for deepcopy
import copy
#math ceiling function
import math

# Generate Model
This command accepts the user input parameters and defines the mesh, element and link connectivity. X direction is longitudinal, Y direction is transverse and Z is vertical. The mesh is rectangular with no checks for rounding or aspect ratio, so the inputs need to be considerate of other geometry that could result in very closely spaced nodes.

The mesh is determined by first locating the 'hard points' that must be included in the mesh. These are the start and end locations of girder properties and deck regions and locations of diaphragms. Once these hard points are determined, the space between them is meshed using a maximim element size according to the user input. 

There are 3 planes of nodes, the deck elevation, the girder elevation, and the boundary condition elevation. Nodes on the deck plane are in the 1,000,000s. Nodes in the girder plate are in the 2,000,000s. Nodes in the boundary conditon plane are in the 3,000,000s. In the y direction, gridlines use the hundred thousands places, in the x direction gridlines use the hundreds places. So node 1,002,003 is in the deck plane (1,000,000) on the second grid line in the y direction (0,002,000) and the third grid line in the x direction (0,000,003). In this way node coordinates are coded into the node number, making connectivity possible by incrementing node numbers. 

Girder element numbers are set as the i node number, link 'element' numbers are set as the j node number (because master nodes 'i' may be re-used where slave nodes 'j' may not) Diaphragm beam elements require an offset to avoid duplicating element numbers with girders. 

In [186]:
def GenerateModel(Mesh_X,Mesh_Y,Deck_inp,Girders_inp,Diaphragms_inp,BC_inp):
    """"
    Function to generate model components (NODES, SHELLS, BEAMS LINKS, BCS)
    
    """
    #find the hard points that must contain a mesh line, then mesh between them according to the mesh size input
    girderpoints_x = list(set([y for x in [Girders_inp[x][::2] for x in Girders_inp] for y in x]))
    deckpoints_x = list(set([y for x in [[Deck_inp[x][0][0],Deck_inp[x][0][1]] for x in Deck_inp] for y in x]))
    diaphragmpoints_x = sorted(Diaphragms_inp.keys())
    
    girderpoints_y = sorted(Girders_inp.keys())
    deckpoints_y = list(set([y for x in [[Deck_inp[x][1][0],Deck_inp[x][1][1]] for x in Deck_inp] for y in x]))
    
    gx = sorted(list(set(deckpoints_x + diaphragmpoints_x + girderpoints_x)))
    gy = sorted(list(set(girderpoints_y + girderpoints_y)))
    
    #find the number of divisions between hard points
    ptsbetweenx = [math.ceil((gx[i+1]-gx[i])/Mesh_X) for i in range(len(gx)-1)]
    ptsbetweeny = [math.ceil((gy[i+1]-gy[i])/Mesh_Y) for i in range(len(gy)-1)]
    
    #make the mesh lines between the hard points (and including the hard points)
    gridx = copy.deepcopy(gx)
    for i, px in enumerate(ptsbetweenx):
        dx = (gx[i+1]-gx[i])/px
        for ii in range(px):
            x = dx*ii + gx[i]
            gridx.append(x)
    gridx = sorted(set(gridx))

    gridy = copy.deepcopy(gy)
    for i, py in enumerate(ptsbetweeny):
        dy = (gy[i+1]-gy[i])/py
        for ii in range(py):
            y = dy*ii + gy[i]
            gridy.append(y)
    gridy = sorted(set(gridy))
    
    print("Mesh is "+str(len(gridx))+" by "+str(len(gridy))+ " nodes")
    
    #mesh the grid
    #node numbering for grid, 1e6 + 1000*yindex + xindex 

    #initialize output dictionaries
    NODES = {}
    #NODES[n]=[x,y,z]
    BEAMS = {}
    #BEAMS[el]=[n1,n2,mat,prop]
    SHELLS = {}
    #SHELLS[el] = {'nodes':[n1,n2,n3,n4],'prop':no}
    LINKS = {}
    #LINKS[l]=[n1,n2...]
    BCS = {}
    #BCS[n] = [dof1,dof2,dof3,dof4,dof5,dof6]
    
    #Make nodes on deck
    for j,y in enumerate(gridy):
        for i,x in enumerate(gridx):
            #start with index 1 for node numbering to avoid a node number 0
            NODES[1000000+1000*(j+1)+(i+1)]={'x':float(x),'y':float(y),'z':float(0)}

    #make the deck shells
    SHELLS = {}
    for d in Deck_inp:
        for j,y in enumerate(gridy[:-1]):
            for i,x in enumerate(gridx[:-1]):
                #print(Deck_inp[d][1][0] , y)
                if all([Deck_inp[d][1][0] <= y, y <= Deck_inp[d][1][1], Deck_inp[d][0][0] <= x, x <= Deck_inp[d][0][1]]):
                    #shell element numbers use the n1 node, (-x,-y node)
                    n1 = 1000000+1000*(j+1)+(i+1)
                    n2 = n1+1
                    n3 = n2+1000
                    n4 = n1+1000
                    SHELLS[n1]={'nodes':[n1,n2,n3,n4],'prop':Deck_inp[d][2]}
            
    #Make nodes on girders and girder elements, 2e6 + 1000*yindex + xindex
    for y in sorted(Girders_inp.keys()):
        gx = Girders_inp[y][::2]
        j = gridy.index(y)
        for i,x in enumerate(gridx):
            #2,000,000s for girder nodes
            n = 2000000+1000*(j+1)+(i+1)
            NODES[n]={'x':float(x),'y':float(y),'z':float(Girders_inp[y][-1])}
            if x<gridx[-1]:
                for g in range(len(gx)-1):
                    if gx[g] <= x and x < gx[g+1]:
                        prop = Girders_inp[y][2*g+1]
                BEAMS[n]=[n,n+1,prop]

    #Make diaphragm elements (4e6)
    for x in sorted(Diaphragms_inp.keys()):
        i =  gridx.index(x)
        gy = sorted(Girders_inp.keys())
        for gj in range(len(gy)-1):
            j1 = gridy.index(gy[gj])
            j2 = gridy.index(gy[gj+1])
            n1 = 2000000+1000*(j1+1)+(i+1)
            n2 = 2000000+1000*(j2+1)+(i+1)
            BEAMS[4000000+1000*(j1+1)+(i+1)]=[n1,n2,Diaphragms_inp[x]]
                
    #Make nodes on BC, 3e6 + 1000*yindex + xindex
    linked=[]
    for coord in sorted(BC_inp.keys()):
        #x and y should already be in gridx, gridy
        x = coord[0]
        y = coord[1]
        z = coord[2]
        i = gridx.index(x)
        j = gridy.index(y)
        n=3000000+1000*(j+1)+(i+1)
        NODES[n]={'x':float(x),'y':float(y),'z':float(z)}
        BCS[n] = BC_inp[coord]
        LINKS[n-1000000]=[n,n-1000000]
        LINKS[n-2000000]=[n,n-2000000]
        linked.append(n-1000000)
    
    #Make Girder to deck links
    for y in sorted(Girders_inp.keys()):
        gx = Girders_inp[y][::2]
        j = gridy.index(y)
        for i,x in enumerate(gridx):
            #2,000,000s for girder nodes
            n = 2000000+1000*(j+1)+(i+1)
            if n not in linked:
                LINKS[n-1000000]=[n,n-1000000]
    
    return NODES,SHELLS,BEAMS,LINKS,BCS


# PlotModel
The plot model function accepts the model definition and returns a 3d scatter and mesh plot in plotly. Currently the mesh plot (of shell elements) cannot be toggled off. The DISP and dispfactor inputs are optional, if provided the model will be rendered in its deformed shape scaled by the dispfactor. 

In [187]:
def PlotModel(NODES,SHELLS,BEAMS,LINKS,BCS,DISP={},dispfactor=0):
    """"
    Function to generate model plot in plotly
    
    """
    if DISP=={}:
        for n in sorted(NODES.keys()): 
            DISP[n]=[0,0,0]
        dispfactor=0
            
    #shells (as a mesh)
    shell_trace=[]
    faces=[]
    shellnodes={}
    counter=0
    x=[]
    y=[]
    z=[]
    for s in sorted(SHELLS.keys()):
        for n in SHELLS[s]['nodes']:
            x.append(NODES[n]['x'] + dispfactor*DISP[n][0])
            y.append(NODES[n]['y'] + dispfactor*DISP[n][1])
            z.append(NODES[n]['z'] + dispfactor*DISP[n][2])
            shellnodes[n]=counter
            counter+=1
    faces=[]
    for s in sorted(SHELLS.keys()):
        faces.append(np.asarray([shellnodes[SHELLS[s]['nodes'][0]],shellnodes[SHELLS[s]['nodes'][1]],shellnodes[SHELLS[s]['nodes'][2]]]))
        faces.append(np.asarray([shellnodes[SHELLS[s]['nodes'][2]],shellnodes[SHELLS[s]['nodes'][3]],shellnodes[SHELLS[s]['nodes'][0]]]))


    points3D=np.vstack((x,y,z)).T
    tri_vertices=list(map(lambda index: points3D[index], faces))
    I,J,K=([triplet[c] for triplet in faces] for c in range(3))
    shell_trace=dict(type='mesh3d',lighting=dict(fresnel=0.2,roughness=0.5,specular=0.05,ambient=0.8,diffuse=0.8),
                     flatshading=True,opacity=0.25,x=x,y=y,z=z,color = 'green', i=I,j=J,k=K,name='Shells',
                     legendgroup='shells')

    lists_coord=[[[T[k][c] for k in range(3)]+[None] for T in tri_vertices] for c in range(3)]
    Xe, Ye, Ze=[functools.reduce(lambda x,y: x+y, lists_coord[k]) for k in range(3)]
    shelledge_trace=dict(type='scatter3d',legendgroup='shells',showlegend=False,x=Xe,y=Ye,z=Ze,
               mode='lines',line=dict(color= 'rgb(150,150,150)',width=1.0),hoverinfo='none')

    #nodes
    x=[NODES[n]['x'] + dispfactor*DISP[n][0] for n in sorted(NODES.keys())]
    y=[NODES[n]['y'] + dispfactor*DISP[n][1] for n in sorted(NODES.keys())]
    z=[NODES[n]['z'] + dispfactor*DISP[n][2] for n in sorted(NODES.keys())] 
    n=sorted(NODES.keys())

    if dispfactor==0:
        node_trace = go.Scatter3d(x=x,y=y,z=z, mode='markers',marker=dict(size=1,color='blue'),name='Nodes',text=n)
    else:
        mxd = max([DISP[n][2] for n in sorted(NODES.keys())])
        mnd = min([DISP[n][2] for n in sorted(NODES.keys())])
        nodecolor = [DISP[n][2] for n in sorted(NODES.keys())]
        text = ["node:"+str(n)+"<br>dx:"+"%5f"%DISP[n][0]+"<br>dy:"+"%5f"%DISP[n][1]+"<br>dz:"+"%5f"%DISP[n][2] for n in sorted(NODES.keys())]
        node_trace = go.Scatter3d(x=x,y=y,z=z,text=text,mode='markers',marker=dict(size=2,color=nodecolor,colorscale='Viridis',
                                  colorbar=dict(title='DZ',x=0,xanchor='right')),name='Nodes')    

    #beams
    DEFAULT_PLOTLY_COLORS=['rgb(31, 119, 180)', 'rgb(255, 127, 14)',
                           'rgb(44, 160, 44)', 'rgb(214, 39, 40)',
                           'rgb(148, 103, 189)', 'rgb(140, 86, 75)',
                           'rgb(227, 119, 194)', 'rgb(127, 127, 127)',
                           'rgb(188, 189, 34)', 'rgb(23, 190, 207)']

    beam_trace=[]
    for b in sorted(BEAMS.keys()):
        if b==sorted(BEAMS.keys())[0]:
            showlegend=True
        else:
            showlegend=False
        beam_trace.append(go.Scatter3d(x=[NODES[BEAMS[b][0]]['x']+ dispfactor*DISP[BEAMS[b][0]][0],NODES[BEAMS[b][1]]['x']+ dispfactor*DISP[BEAMS[b][1]][0]],
                                       y=[NODES[BEAMS[b][0]]['y']+ dispfactor*DISP[BEAMS[b][0]][1],NODES[BEAMS[b][1]]['y']+ dispfactor*DISP[BEAMS[b][1]][1]],
                                       z=[NODES[BEAMS[b][0]]['z']+ dispfactor*DISP[BEAMS[b][0]][2],NODES[BEAMS[b][1]]['z']+ dispfactor*DISP[BEAMS[b][1]][2]],
                                       mode='lines',legendgroup='beams',showlegend=showlegend,text=b,
                                       name='Beams',line=dict(color=DEFAULT_PLOTLY_COLORS[BEAMS[b][2]])))

    link_trace=[]
    for l in sorted(LINKS.keys()):
        if l==sorted(LINKS.keys())[0]:
            showlegend=True
        else:
            showlegend=False   
        link_trace.append(go.Scatter3d(x=[NODES[LINKS[l][0]]['x']+ dispfactor*DISP[LINKS[l][0]][0],NODES[LINKS[l][1]]['x']+ dispfactor*DISP[LINKS[l][1]][0]],
                                       y=[NODES[LINKS[l][0]]['y']+ dispfactor*DISP[LINKS[l][0]][1],NODES[LINKS[l][1]]['y']+ dispfactor*DISP[LINKS[l][1]][1]],
                                       z=[NODES[LINKS[l][0]]['z']+ dispfactor*DISP[LINKS[l][0]][2],NODES[LINKS[l][1]]['z']+ dispfactor*DISP[LINKS[l][1]][2]],
                                       mode='lines',legendgroup='links',showlegend=showlegend,name='Links',text=l,line=dict(color='black')))


    #layout
    noaxis=dict(showbackground=False,showline=False,zeroline=False,showgrid=False,showticklabels=False,title='')
    layout=dict(title='Model',scene=dict(aspectmode='data',xaxis=noaxis,yaxis=noaxis,zaxis=noaxis))
    fig = go.Figure(data=[node_trace]+beam_trace+link_trace+[shell_trace]+[shelledge_trace],layout=layout)
    py.iplot(fig)
    return None
      

# BuildOpenSEES
This function converts the generic nodal coordinates and connectivity into an OpenSEES model. There are assumptions in here for element type and beam orientation. 

Beam element orientation is described here
__[http://opensees.berkeley.edu/wiki/index.php/Linear_Transformation](http://opensees.berkeley.edu/wiki/index.php/Linear_Transformation)__

element types are described here
__[http://opensees.berkeley.edu/wiki/index.php/Element_Command] (http://opensees.berkeley.edu/wiki/index.php/Element_Command)__



In [188]:
def BuildOpenSEES(NODES,SHELLS,BEAMS,LINKS,BCS,Sections_inp,DeckSections_inp,Materials_inp,LOAD):
    """"
    Function to generate model in Opensees
    
    """ 

    # remove existing model
    opensees.wipe()

    # set modelbuilder, basic 3d model
    opensees.model('basic', '-ndm', 3)
    #---------------------------------------------------------------------------------------
    # create nodes

    for n in sorted(NODES.keys()):
        opensees.node(int(n), *[float(NODES[n]['x']), float(NODES[n]['y']),float(NODES[n]['z'])])

    #---------------------------------------------------------------------------------------
    # boundary conditions

    for n in sorted(BCS.keys()):
        opensees.fix(int(n),*BCS[n])

    #---------------------------------------------------------------------------------------
    # define materials

    #for m in MATERIALS:
    #    opensees.nDMaterial('ElasticIsotropic', int(m), float(MATERIALS[m]['E']),
    #                        float(MATERIALS[m]['Nu']), float(MATERIALS[m]['Rho']))

    #---------------------------------------------------------------------------------------    
    # define beam elements 


    #transfArgs=[$vecxzX,$vecxzY,$vecxzZ]
    transfTag_G=1
    transfArgs_G=[0.0,-1.0,0.0]
    opensees.geomTransf("Linear", int(transfTag_G),*transfArgs_G)
    transfTag_D=2
    transfArgs_D=[1.0,0.0,0.0]
    opensees.geomTransf("Linear", int(transfTag_D),*transfArgs_D)

    for b in BEAMS:
        prop=BEAMS[b][2]
        mat=Sections_inp[prop]['mat']
        if prop == 1:
            transfTag = transfTag_D
        else:
            transfTag = transfTag_G
        '''
        opensees.element('elasticBeamColumn', int(b), *[BEAMS[b][0],BEAMS[b][1]],
                         SECTIONS[prop]['A'],MATERIALS[mat]['E'], MATERIALS[mat]['G'],  
                         SECTIONS[prop]['J'], SECTIONS[prop]['Iy'],SECTIONS[prop]['Ix'],
                         transfTag,'-mass',float(SECTIONS[prop]['A']*MATERIALS[mat]['Rho']),'-cmass')
        '''
        opensees.element('ElasticTimoshenkoBeam', int(b), *[BEAMS[b][0],BEAMS[b][1]],
                         Materials_inp[mat]['E'], Materials_inp[mat]['G'], Sections_inp[prop]['A'], 
                         Sections_inp[prop]['J'], Sections_inp[prop]['Iy'],Sections_inp[prop]['Ix'], Sections_inp[prop]['Ay'],
                         Sections_inp[prop]['Ax'],transfTag,'-mass',float(Sections_inp[prop]['A']*Materials_inp[mat]['Rho']),"-cMass")


    #---------------------------------------------------------------------------------------
    # define shell sections
    for d in sorted(DeckSections_inp.keys()):
        prop = d
        mat = DeckSections_inp[prop]['mat']
        nsm = DeckSections_inp[prop]['nsm']
        thick = DeckSections_inp[prop]['thick']

        opensees.section('ElasticMembranePlateSection', int(d), float(Materials_inp[mat]['E']),
                float(Materials_inp[mat]['Nu']+nsm/thick),
                float(thick), float(Materials_inp[mat]['Rho']))

    # define shell elements as ShellMITC4 elements  (do these have membrane action, or just bending?)
    for s in sorted(SHELLS.keys()): 
        #ShellMITC4
        opensees.element('ShellMITC4',int(s),*SHELLS[s]['nodes'],int(SHELLS[s]['prop']))
        #ShellDKGQ 
        #opensees.element('ShellDKGQ',int(s),*SHELLS[s]['nodes'],int(SHELLS[s]['prop']))
        

    #---------------------------------------------------------------------------------------    
    #define links    
    for l in sorted(LINKS.keys()):
        if len(LINKS[l])==3:
            opensees.rigidDiaphragm(int(2), int(LINKS[l][0]), *[int(LINKS[l][1]),int(LINKS[l][2])])
        elif len(LINKS[l])==2:
            opensees.rigidLink('beam', LINKS[l][0], LINKS[l][1])

    #---------------------------------------------------------------------------------------
    # define loads
    # create TimeSeries
    opensees.timeSeries("Constant", 1)

    # create a plain load pattern
    opensees.pattern("Plain", 1, 1)

    # unit point load at node 1001045 in -z direction
    opensees.load(int(LOAD[0]), *[0.0,0.0,float(LOAD[1]),0.0,0.0,0.0])

    return None

# RunOpenSEES

This function defines the run options, most of them are hard coded. The system option is available as optional user input. 
__[http://opensees.berkeley.edu/wiki/index.php/System_Command] (http://opensees.berkeley.edu/wiki/index.php/System_Command)__

In [ ]:
def RunOpenSEES(system="BandGeneral"):
    """"
    Function to run model in OpenSEES
    
    """
    # create SOE
    opensees.system(system)

    # create DOF number
    opensees.numberer("RCM")

    # create constraint handler
    opensees.constraints("Transformation")

    # create integrator
    opensees.integrator("LoadControl", 1.0)

    # create algorithm
    opensees.algorithm("Linear")

    # create analysis object
    opensees.analysis("Static")
    
    #record reactions
    opensees.recorder('Node', '-file', 'nodes.txt','-time', '-node', *[sorted(BCS.keys())], '-dof', *[1,2,3,4,5,6], 'reaction')
    
    #run the analysis
    res = opensees.analyze(1)
    
    return res

# PlotGirderResults

This function generates a 3d scatter plot of beam elements, with an overlay using the vertical axis to report a specified beam element output quantity. Output quanties are: Fx Fy Fz Mx My Mz  (needs a reference).

In [ ]:
def PlotGirderResults(NODES,BEAMS,res,dof):
    """
    Function to plot results
    """
    
    DEFAULT_PLOTLY_COLORS=['rgb(31, 119, 180)', 'rgb(255, 127, 14)',
                           'rgb(44, 160, 44)', 'rgb(214, 39, 40)',
                           'rgb(148, 103, 189)', 'rgb(140, 86, 75)',
                           'rgb(227, 119, 194)', 'rgb(127, 127, 127)',
                           'rgb(188, 189, 34)', 'rgb(23, 190, 207)']
    beam_trace=[]
    for b in sorted(BEAMS.keys()):
        if b==sorted(BEAMS.keys())[0]:
            showlegend=True
        else:
            showlegend=False
        beam_trace.append(go.Scatter3d(x=[NODES[BEAMS[b][0]]['x'],NODES[BEAMS[b][1]]['x']],
                                       y=[NODES[BEAMS[b][0]]['y'],NODES[BEAMS[b][1]]['y']],
                                       z=[NODES[BEAMS[b][0]]['z'],NODES[BEAMS[b][1]]['z']],
                                       mode='lines',legendgroup='beams',showlegend=showlegend,text=b,
                                       name='Beams',line=dict(color=DEFAULT_PLOTLY_COLORS[BEAMS[b][2]])))
    dy = max([NODES[n]['y'] for n in NODES.keys()]) - min([NODES[n]['y'] for n in NODES.keys()])
    dr = max([res[b][dof] for b in res.keys()]) - min([res[b][dof] for b in res.keys()])
    sf = dy/dr
    res_trace=[]
 
    cmax=None
    cmin=None
    for b in sorted(BEAMS.keys()):
        if cmax==None:
            cmax = max([res[b][dof],-res[b][dof+6]])
            cmin = min([res[b][dof],-res[b][dof+6]])
        else:
            cmax = max([cmax,res[b][dof],-res[b][dof+6]])
            cmin = min([cmin,res[b][dof],-res[b][dof+6]])
        
    for b in sorted(BEAMS.keys()):
        if b==sorted(BEAMS.keys())[0]:
            showlegend=True
        else:
            showlegend=False
        res_trace.append(go.Scatter3d(x=[NODES[BEAMS[b][0]]['x'],NODES[BEAMS[b][1]]['x']],
                                      y=[NODES[BEAMS[b][0]]['y'],NODES[BEAMS[b][1]]['y']],
                                      z=[NODES[BEAMS[b][0]]['z']+res[b][dof]*sf,NODES[BEAMS[b][1]]['z']+res[b][dof+6]*-sf],
                                      text=[res[b][dof],-res[b][dof+6]],
                                      mode='lines+markers',
                                      legendgroup='res',
                                      showlegend=showlegend,
                                      name='Results',
                                      #line=dict(color='black')
                                      line=dict(color=[res[b][dof],-res[b][dof+6]],colorscale='Viridis',cmin=cmin,cmax=cmax,width=6),
                                      marker=dict(showscale=True,colorbar=dict(tickfont=dict(size=20),x=0.00,xanchor='left',showticklabels=True),
                                                  size=0,symbol='circle',color=[res[b][dof],-res[b][dof+6]],colorscale='Viridis',cmin=cmin,cmax=cmax)))
    '''
    (x=x,
     y=y,
     z=zmax,
     text=hovrtextmax,
     hoverinfo='text+name',
     mode='lines+markers',
     
     marker=dict(showscale=True,colorbar=dict(tickfont=dict(size=20),title='Rating Factor',titlefont=dict(size=20),
                               x=0.00,xanchor='left',showticklabels=True,tickvals=tickvals,ticktext=ticktext),
                 size=0,symbol='circle',color=colormax,colorscale='Viridis',cmin=0.,cmax=maxcolor),
     
     line=dict(color=colormax,colorscale='Viridis',cmin=0.,cmax=maxcolor,width=6),
      
     legendgroup='RF',name=method +" Rating Factor",visible=True)
     '''
       
        
    #layout
    noaxis=dict(showbackground=False,showline=False,zeroline=False,showgrid=False,showticklabels=False,title='')
    layout=dict(title='Model',scene=dict(aspectmode='data',xaxis=noaxis,yaxis=noaxis,zaxis=noaxis))
    fig = go.Figure(data=beam_trace+res_trace,layout=layout)
    py.iplot(fig)
    return None    

# User Inputs

The user's inputs must be in consistent units. (in and lbf is used in this example)
 - Mesh_X: the maximum shell element dimension in the longitudinal direction
 - Mesh_Y: the maximum shell element dimension in the transverse direction
 - Deck_inp: a dictionary defining the deck regions by coordinates and property number
 - DeckSection_inp: a dictionary defining deck section properties
 - Girders_inp: a dictionary defining each girder line, inputs are the X,prop,X,prop,X.... as many as needed to define the full girder line, followed by Z coordinate. (need to revise to allow different properties at different elevations)
 - BC_inp: boundary condtion inputs by coordinate, these x & y coordinates need to correspond to the other geometry inputs. Dof inputs are TX, TY, TZ, RX, RY, RZ. 1 is restrained, 0 is free.
 - Sections_inp: a dictionary defining beam cross section parameters. (Should be revised to use y and z since per __[http://opensees.berkeley.edu/wiki/index.php/Linear_Transformation](http://opensees.berkeley.edu/wiki/index.php/Linear_Transformation)__ )
 - Materials_inp: a dictionary defining material properties. 

In [ ]:
# -----------------------------
#Inputs
#consistent units: in,lb
# -----------------------------

#Mesh
Mesh_X=10
Mesh_Y=10

#Deck
Deck_inp={}
#Deck_inp[No]=[(Xstart,Xend),(Ystart,Yend),prop]
Deck_inp[1] = [(0,780),(-143,143),1]

#DECK PROPERTIES
DeckSections_inp={}
DeckSections_inp[1]={"thick":7.25,"nsm":0,"mat":2}   

#Girders
Girders_inp={}
#Girders_inp[Y]=[X,prop,X,prop,X,prop,X,Z]
Girders_inp[-132.0]=[0.,2,150.,3,630.,2,780.,-24.]
Girders_inp[-44.0]= [0.,2,162.,4,618.,2,780.,-24.]
Girders_inp[44.0]=  [0.,2,162.,4,618.,2,780.,-24.]
Girders_inp[132.0]= [0.,2,150.,3,630.,2,780.,-24.]

#Boundary Conditions
BC_inp={}
#BC_inp[(x,y,z)]=[dof1,dof2,dof3,dof4,dof5,dof6] (1 for restrained, 0 for free)
BC_inp[(0.,-132.,-36.)] = [1,1,1,0,0,0]
BC_inp[(0.,-44.,-36.)] = [1,1,1,0,0,0]
BC_inp[(0.,44.,-36.)] = [1,1,1,0,0,0]
BC_inp[(0.,132.,-36.)] = [1,1,1,0,0,0]
BC_inp[(780.,-132.,-36.)] = [0,0,1,0,0,0]
BC_inp[(780.,-44.,-36.)] = [0,0,1,0,0,0]
BC_inp[(780.,44.,-36.)] = [0,0,1,0,0,0]
BC_inp[(780.,132.,-36.)] = [0,0,1,0,0,0]

#Diaphragms
Diaphragms_inp={}
#Diaphragms_inp[X]=prop
Diaphragms_inp[0.0]=1
Diaphragms_inp[195.0]=1
Diaphragms_inp[390.0]=1
Diaphragms_inp[585.0]=1
Diaphragms_inp[780.0]=1

#BEAM SECTIONS
Sections_inp={}
#Sections_inp[i] = {"A","Ix","Iy","J","Ax","Ay"}
Sections_inp[1] = {"A":12.475,  "Ix": 549.035, "Iy": 15.6833, "J": 1.10832, "Ax": 1.66727,"Ay": 7.40825,"mat":1}
Sections_inp[2] = {"A":37.8712, "Ix": 6607.75, "Iy": 217.235, "J": 6.73246, "Ax": 16.6574,"Ay": 18.2646,"mat":1}
Sections_inp[3] = {"A":45.6822, "Ix": 8414.14, "Iy": 288.743, "J": 18.3722, "Ax": 23.2446,"Ay": 18.6911,"mat":1}
Sections_inp[4] = {"A":44.5148, "Ix": 8277.46, "Iy": 276.798, "J": 15.5185, "Ax": 22.126 ,"Ay": 18.7483,"mat":1}

#MATERIALS
Materials_inp={}
#MATERIALS
#steel
Materials_inp[1] = {"E":29000000.0,"Nu":0.29,"Rho":490/12.**3}
#conc
Materials_inp[2] = {"E":57000*(3000)**0.5,"Nu":0.2,"Rho":150/12.**3}
for m in Materials_inp:
    Materials_inp[m]['G'] = Materials_inp[m]['E']/(2*(1+Materials_inp[m]['Nu']))
  

## Generate then plot the model

(may need to hover mouse over the plot for it to appear)

In [ ]:
NODES,SHELLS,BEAMS,LINKS,BCS = GenerateModel(Mesh_X,Mesh_Y,Deck_inp,Girders_inp,Diaphragms_inp,BC_inp)
print('Nodes=',len(NODES))
print('Shells=',len(SHELLS))
print('Beams=',len(BEAMS))
print('Links=',len(LINKS))
print('BCs=',len(BCS))

Mesh is 83 by 28 nodes
Nodes= 2664
Shells= 2214
Beams= 343
Links= 340
BCs= 8


In [ ]:
PlotModel(NODES,SHELLS,BEAMS,LINKS,BCS)

## Chose node to load then build and run OpenSEES model

In [ ]:
LOAD=[1001045,-1000]
BuildOpenSEES(NODES,SHELLS,BEAMS,LINKS,BCS,Sections_inp,DeckSections_inp,Materials_inp,LOAD)

In [ ]:
# perform the analysis
RunOpenSEES()

## Export the model to json and extract results

In [ ]:
opensees.printModel('-file','out.json')

In [ ]:
opensees.reactions()
#extract results
REACTIONS={}
for n in sorted(BCS.keys()):
    REACTIONS[n] = opensees.nodeReaction(n)
    
DISP={}
for n in sorted(NODES.keys()):
    DISP[n] = opensees.nodeDisp(int(n))

BEAMFORCES={}
for b in sorted(BEAMS.keys()):
    #BEAMFORCES[b] = opensees.eleForce(int(b))
    BEAMFORCES[b] = opensees.eleResponse(int(b),'forces')

## Plot Results

(may need to hover mouse over the plot for it to appear)

In [ ]:
PlotModel(NODES,SHELLS,BEAMS,LINKS,BCS,DISP,10000)

In [ ]:
#plot axial forces
PlotGirderResults(NODES,BEAMS,BEAMFORCES,0)

Strand7 run shows 2813 kip (Tension) under the load, and 1583 kip (compression) at the support.

In [ ]:
#plot shear forces
PlotGirderResults(NODES,BEAMS,BEAMFORCES,2)

In [ ]:
#plot bending moment
PlotGirderResults(NODES,BEAMS,BEAMFORCES,4)

Things to check:
- check that links are rigid
- check that shells have in-plane shear


Put in a 'dummy' trace in the girder results so theres only 1 color bar